# Case Study: Hedging Oil Price Exposure As An E&P

In [1]:
import pandas as pd
import numpy as np


import plotly.io as pio

from IPython.display import display

import warnings


# import hedging functions
import brent_hedging_functions as hf


warnings.filterwarnings("ignore")
pio.templates.default = "plotly_white"
pio.renderers.default = "notebook"
pd.set_option("display.max_columns", None)
COMDTY_CODES = {"brent": "CB"}
# cme month codes dict
cme_month_codes = {
    1: "F",
    2: "G",
    3: "H",
    4: "J",
    5: "K",
    6: "M",
    7: "N",
    8: "Q",
    9: "U",
    10: "V",
    11: "X",
    12: "Z",
}

## About The Teaching Assistant

Viren Desai is the teaching assistant for this course. He has prior experience as a *finance and strategy consultant* specializing in the *upstream energy sector*, developing *financial models and data analytics frameworks* to support risk management, capital allocation, and strategic decision-making for companies and investors in the energy space.


**Clients & Industry Focus**
His consulting practice primarily worked with:

1. **Oil & Gas Producers**
   - Also known as *Exploration & Production (E&P) companies* or *upstream operators*.
   - These firms extract, process, and sell crude oil, natural gas, and natural gas liquids (NGLs).

2. **Private Equity Firms**
   - Investors that *own, acquire, or manage upstream energy companies*.
   - Require *robust financial models* for valuation, risk assessment, and capital allocation.


**Core Areas of Expertise**
He applied *quantitative finance, risk modeling, and economic analysis* to help upstream energy firms make *data-driven financial decisions*. Key areas of focus included:

1. **Corporate Hedging Advisory & Risk Modeling**
   - Structuring and evaluating commodity hedging strategies
   - Assessing hedge effectiveness and risk exposure

2. **Data Modeling, Integration & Analytics**
   - Automating financial and operational data workflows
   - Developing analytical tools for market and company-level insights

3. **Financial Strategy & Capital Allocation**
   - Evaluating investment opportunities and capital structuring
   - Scenario modeling for debt, equity, and cash flow planning

4. **Corporate Valuation & Cash Flow Modeling**
   - Building financial projections for M&A, fundraising, and strategic planning
   - Quantifying the impact of commodity price fluctuations on valuation

5. **Macroeconomic & Market Analysis**
   - Assessing trends in interest rates, inflation, and economic cycles
   - Understanding supply, demand, and pricing dynamics in global energy markets


**Background & Experience**

15+ Years in finance, energy, and investment strategy:

- **Energy Investment Banking (5 years):** Focused on M&A, capital markets, and financial advisory at *Morgan Stanley* and *Jefferies*

- **Private Credit & Structured Investments (3 years):** Generalist private credit investing at *Deerpath Capital Management* and *Crestline Investors*

- **Upstream Energy Finance Leadership (4 years):** VP of Finance at *Triple Crown Resources*, a *private equity-backed upstream operator*

- **Financial Analytics & Decision Support (3 years):** Developing *financial models & strategic tools* for energy firms as an *independent consultant*


**Education**
- 🎓 *BA in Mathematical Economic Analysis* – *Rice University (2010)*
- 🎓 *MS in Financial Mathematics* – *University of Chicago (2024)*

---

## Case Study: Hedging Oil Price Exposure As An E&P
<br>

### What is an "E&P"?

- **Exploration and production businesses in the oil and gas sector are companies that extract oil and gas from the ground, and sell these commodities to the market**. Extraction is via the drilling and operation of oil and gas wells. Also called "upstream" companies.

- Employ a broad range of skillsets (PhDs/Engineering masters for scientific and geological work, MBAs / finance for management, GEDs or simply years of experience for "on-the-ground" field work).

- Capital-intensive businesses, challenging to operate for a variety of reasons, but can be very lucrative for shareholders if growth and financial risk are managed well.

- **Financial risk** $\rightarrow$ *probability of loss of investment*. For E&Ps, this investment risk arises from large **minimum capital investment** required to drill and operate an oil or gas well:

    1. Seismic and geological studies of an area to assess how much oil and gas exists underground can cost anywhere from **\$200k - \$2 million+**, depending on the complexity.

    2. Drilling a *single oil or gas well* can cost **\$5mm - \$25mm onshore US**, spent over several months. Offshore oil and gas wells can cost **\$150 million+** (these are considered <u>capital expenditures</u>).

    3. Beyond this, there are operating costs, initial processing costs for the company, as well as pipeline or truck transportation expenses.

    4. Due to the asset-heavy nature of these businesses, they can typically raise leverage from banks (and more recently, credit funds). Managing this leverage effectively requires a business skillset.

    5. Furthermore, the business sells its products at a price reflective of commodity futures markets (with each of oil, natural gas, etc. comprising a separate market, each with its own dynamics).

<br>

### Primary Business Objectives
1. **Grow cash flow** via higher production of oil, gas, and NGLs (ethane, propane, butane, natural gasoline).
2. **Minimize the risk around future cash flows** by de-risking key business areas (geological, financial).
3. **Increase net asset value (equity value)**—typically a byproduct of executing the first two objectives well.

<br>

<i><b><font color='blue'>Essentially, the E&P management team is trying to maximize the <u>Risk-Adjusted Return on Capital (RAROC)</u> for their investors. <br><br> In other words, they aim to <u>maximize expected future cash inflows</u> while <u>minimizing the risk around those future cash inflows</u>.<br><br> Maximizing RAROC is essentially a business equivalent of maximizing the "Sharpe Ratio" of an investment portfolio!</font></b></i>

<br>

**Sharpe Ratio for a Portfolio (Reminder)**

- A higher Sharpe Ratio indicates better risk-adjusted performance. The Sharpe Ratio is defined as:

$$
\text{Sharpe Ratio}_{\text{portfolio}} = \frac{R_p - R_f}{\sigma_p}
$$

where:
- $R_p$ = Expected portfolio return
- $R_f$ = Risk-free rate
- $\sigma_p$ = Standard deviation of portfolio returns

<br>

**Risk-Adjusted Return on Capital (Business)**

- A higher RAROC indicates better risk-adjusted business performance.

$$
\begin{align}
\textcolor{teal}{\text{Risk-Adjusted Return on Capital}_{\text{business}}} &=
\frac{\textcolor{blue}{\text{Expected Return}} - \textcolor{red}{\text{Risk-Free Return}}}{\text{Expected Deviation of Returns}} \tag{1} \\
\textcolor{blue}{\text{Expected Return}} &=
\frac{\textcolor{green}{\text{Expected Future Revenues}} - \textcolor{orange}{\text{Expected Future Costs}}}{\text{Capital Invested}} \tag{2} \\
\textcolor{green}{\text{Expected Future Revenues}} &=
(\textcolor{purple}{\text{Expected Future Commodity Prices}} \times \text{Expected Future Volume of Oil/Gas/NGLs}) + \textcolor{purple}{\text{Net Cash Flow Impact of Hedging}} \tag{3}
\end{align}
$$

<br>

---

### Primary Source of <u>Revenue Risk</u>: Commodity Prices

<br>

Viren helps clients reduce uncertainty around **Equation (3)**:

$$
\begin{align}
\textcolor{green}{\text{Expected Future Revenues}} &=
(\textcolor{purple}{\text{Expected Future Commodity Prices}} \times \text{Expected Future Volume of Oil/Gas/NGLs}) + \textcolor{purple}{\text{Net Cash Flow Impact of Hedging}} \tag{3} \\
\end{align}
$$

<br>

### Defining The Corporate Hedging Problem: How To Reduce Price Risk (Where Revenue = Price x Volume)

- **The challenge is captured in Equation (3) and the futures term structure below (for Brent oil, Henry Hub natural gas, and Propane, a natural gas liquid/NGL)**

![Brent Price History - Last 11 Days](./assets/2025-02-13_strip_price_history_CY.png)

![Henry Hub Price History - Last 11 Days](./assets/2025-02-13_strip_price_history_NG.png)

![Propane Price History - Last 11 Days](./assets/2025-02-13_strip_price_history_B0.png)

<br>

---

### Managing Revenue Risk Via Hedging
- **E&Ps have a natural <u>long</u> exposure to oil, natural gas, and NGL prices**: Their (unhedged) revenue is therefore stochastic and subject to factors influencing oil and gas prices, including:
    - Supply, demand, storage
    - Geopolitics
    - Interest rates
    - Speculative interest

- **Hedging tools** include:
    - **Calls**
    - **Puts**
    - **Fixed price swaps**
    - **(Rarely) Exotic structures**

- Many hedging decisions are made **without fully considering the underlying statistical properties** of the commodities being hedged.

<br>

### Benefits of Risk Management
1. **Attract greater capital investment** $\rightarrow$ investors prefer companies demonstrating superior financial risk management.
2. **Stronger IPO potential** $\rightarrow$ public investors seek companies with predictable multi-year cash flows.
3. **Higher valuation multiples (P/E ratios)** $\rightarrow$ companies with **higher RAROC** command **higher premiums** in financial markets.
4. **Increased wealth for employees and shareholders**

<br>


---


## This Lecture:

<font color='red' size=6>☐</font> 1. Model an E&P as a **long position in Brent oil futures (CME: CY)**.

<font color='red' size=6>☐</font> 2. Work with **real option prices & futures data** for Brent oil.

<font color='red' size=6>☐</font> 3. Use **option delta** to approximate the probability of an option expiring in-the-money.

<font color='red' size=6>☐</font> 4. Use **option delta** to define acceptable risk ranges for the hedging program (e.g., 80% probability of options expiring worthless).

<font color='red' size=6>☐</font> 5. Design a hedging strategy to **lock in a price floor** for oil using put options.

<font color='red' size=6>☐</font> 6. Attempt to **make the hedge costless** by selling call options (i.e., constructing a **costless collar**).

<font color='red' size=6>☐</font> 7. **Validate option pricing models** using **Monte Carlo simulation** of Brent futures with implied volatility.

<br>

## Homework Assignment:
- Replicate this exercise for **SPX options**.

---
## A Brief Review Of The Option Market and Option Pricing

**! Important !**

### **Model Inputs for Option Pricing**

1. <font color='blue'>**The underlying security's current price**</font> _(Brent, in this case)_ → **Known / observable**.

2. <font color='blue'>**The option strike price**</font> → **Chosen by the investor**; market makers provide quotes for commonly used strikes.

3. <font color='blue'>**Time to maturity**</font> → **Chosen by the investor**; Brent options are typically quoted in monthly maturities.

4. <font color='blue'>**The risk-free rate**</font> → **Observable** (commonly estimated using U.S. Treasuries of similar maturity).

5. <font color='red'>**The implied volatility**</font> → **Not observable**; it is inferred from market prices by solving the **BSM equation**.


<br>

*All inputs to the BSM model are known or observable in the market, except for one:  **_implied volatility_** _(which must be inferred from market prices)_.*


<br>

---
## Call Options
- Can buy or sell call options for a price (determined by the market; also called the option "premium" or "cost").
- Option prices vary based on current Brent price level, and future expectations of movement.
- Investor chooses strike price, time to expiry (contract maturity), and whether to buy (go long) or sell (short) the call option.
- If **Brent price at expiry > strike price**, a call option is **in-the-money ("ITM")**, and the **buyer receives (Brent – strike)** at settlement.
    - Net of upfront cost, the call option buyer's **Payoff = (Brent – strike) – upfront cost**.
- If **Brent price at expiry <= strike price**, a call option is **out-of-the-money ("OTM")**, and **expires worthless**.
    - The call option buyer's **Payoff = – upfront cost** $\rightarrow$ The buyer loses the amount paid for the option.

<br>

### Black-Scholes Formula For European Call Option Pricing

$$
C(S, K, \sigma, r,  T) = S \Phi (d_1) - K e^{-rT} \Phi (d_2)
$$

where:

- $S$ = Price of underlying
- $K$ = Option strike price
- $\Phi(.)$ = CDF of Standard Normal Distribution
- $\sigma$ = Implied volatility (IV) of the underlying asset
- $r$ = Risk-free rate
- $T$ = Time remaining to expiry
- $d_1 = \frac{\ln\left(\frac{S}{K}\right) + \left(r + \frac{\sigma^2}{2}\right)T}{\sigma \sqrt{T}}$
- $d_2 = d_1 - \sigma \sqrt{T}$

<br>

### Call Option Payoff at Expiry

<table>
<tr>
  <td>

  | Parameter                 | Value              |
  |---------------------------|--------------------|
  | **Brent Price**           | $80.00 per Barrel |
  | **Option Strike Price**   | $90.25 per Barrel |
  | **Time to Maturity**      | 0.5 years (6-month option) |
  | **Annual Risk-Free Rate** | 4.3% (6 mo. U.S. Treasury Bill Yield) |
  | **Annualized Volatility** | 27.44% (As of 1/23/25) |
  | **Option Price**          | $3.19 per Barrel |

  </td>
</tr>
</table>

In [2]:
call_payoffs = hf.show_call_option_payoff(S=80, K=90.25, sigma=0.2744, r=0.045, T=0.5)

---
## Put Options

Same as call options:

- Can buy or sell put options for a price (determined by the market; also called the option "premium" or "cost").
- Option prices vary based on current Brent price level, and future expectations of movement.
- Investor chooses strike price, time to expiry (contract maturity), and whether to buy (go long) or sell (short) the put option.

Different from call options:
- If **Brent price at expiry < strike price**, a put option is **in-the-money ("ITM")**, and the buyer receives (strike – Brent) at settlement.
    - Net of upfront cost, the put option buyer's **Payoff = (strike – Brent) – upfront cost**.
- If **Brent price at expiry >= strike price**, a put option is **out-of-the-money ("OTM")**, and expires worthless.
    - The put option buyer's **Payoff = – upfront cost** $\rightarrow$ The buyer loses the amount paid for the option.

<br>

### Black-Scholes Formula For European Put Option Pricing

$$
P(S, K, \sigma, r,  T) = K e^{-rT} \Phi (-d_2) - S \Phi (-d_1)
$$

where:

- $S$ = Price of underlying
- $K$ = Option strike price
- $\Phi(.)$ = CDF of Standard Normal Distribution
- $\sigma$ = Implied volatility (IV) of the underlying asset
- $r$ = Risk-free rate
- $T$ = Time remaining to expiry
- $d_1 = \frac{\ln\left(\frac{S}{K}\right) + \left(r + \frac{\sigma^2}{2}\right)T}{\sigma \sqrt{T}}$
- $d_2 = d_1 - \sigma \sqrt{T}$


<br>

### Put Option Payoff at Expiry

<table>
<tr>
  <td>

  | Parameter                 | Value              |
  |---------------------------|--------------------|
  | **Brent Price**           | $80.00 per Barrel |
  | **Option Strike Price**   | $75.00 per Barrel |
  | **Time to Maturity**      | 0.5 years (6-month option) |
  | **Annual Risk-Free Rate** | 4.3% (6 mo. U.S. Treasury Bill Yield) |
  | **Annualized Volatility** | 27.44% (As of 1/23/25) |
  | **Option Price**          | $3.17 per Barrel |

  </td>
</tr>
</table>

In [3]:
put_payoffs = hf.show_put_option_payoff(S=80, K=75, sigma=0.2744, r=0.045, T=0.5)

---
## The Costless Collar: A "Free" Floor on Oil Prices

In [4]:
collar_payoff = hf.build_costless_collar(
    put_payoffs, call_payoffs, put_strike=75, call_strike=90.25
)
collar_payoff = hf.add_S_payoff(collar_payoff, S0=80, name="Brent")

---

**Observation 1: Locking in the floor is a dynamic decision. Why?**

**Observation 2: A high floor is a contradictory objective with a high ceiling price. Why?**


<br>

---

### Question 1: How Do We Know What Strikes / Expiries To Hedge?

**(Partial) Answer**: We need some estimate of the probability of the underlying price crossing the call or put strikes (i.e. the prob. of the option expiring in-the-money, $P_{ITM}$).

<br>


---
### Question 2: Is There A Metric That Allows Us To Estimate This Probability, Based on Option Prices?

**Quick Answer**: Yes - the option delta is a good estimate.

**Less Quick Answer**: Yes - $\Phi(d_2)$, which is the risk-neutral probability of an option expiring ITM.:

But:

 1) it's a bit more involved to calculate,

 2) call and put deltas are freely available from many data providers,

 3) $\Phi(d_2)$ is typically fairly close to $\Phi(d_1)$, particularly for options near-the-money or close to expiry ($T\rightarrow 0$),

 4) We can approximate $\Phi(d_2)$ with a first-order Taylor approximation of $\Phi(.)$, since we know the value of the call option delta $\Phi(d_1)$ (and of course, the put option delta $(\Phi(d_1) - 1)$

...and if you *really* want to know the relationship:

$$
\begin{aligned}
d_1 &= \frac{ln(S/K) + (r + \frac{\sigma^2}{2})T}{\sigma\sqrt{T}} \\
d_2 &= \frac{ln(S/K) + (r - \frac{\sigma^2}{2})T}{\sigma\sqrt{T}} \\
\\
\Rightarrow d_2 &= d_1 - \sigma\sqrt{T}  \rightarrow \textit{Note that } d_2 \le d_1 \\
\\
\\
\text{Since }(d_1 - d_2) &= \sigma\sqrt{T} \text{, we can use a first order Taylor approximation to estimate }\Phi(d_2)
\\
\\
\Rightarrow \Phi(d_2) &\approx \Phi(d_1) - \Phi'(d_1) (d_2 - d_1) \\
\\
\Rightarrow \Phi(d_2) &\approx \Phi(d_1) - \frac{e^{-d_1^2/2}}{\sqrt{2\pi}} (\sigma\sqrt{T}) \\
\\
\\
\Rightarrow \Phi(d_2) &\approx \Delta_C - \textit{Adj. Factor} \\
\Rightarrow \Phi(d_2) &\approx \Delta_P - (\textit{Adj. Factor} - 1) \\
\end{aligned}
$$

<br>


$$
\begin{aligned}
\text{For call options} \rightarrow \Delta_C = \frac{\partial C}{\partial S}&=\Phi(d_1) \\
\text{For put options} \rightarrow \Delta_P = \frac{\partial P}{\partial S}&=\Phi(d_1)-1
\\
\\
\textit{where: } \Phi(d_1) \text{ is the standard normal CDF evaluated at } &d_1
\end{aligned}
$$

<br>

<br>

---
**For the rest of this lecture and the homework assignment, we will assume the **option delta** is an estimate of the probability of that option expiring ITM.**
<br>

### Option Deltas

1. **Call Option Delta**: Measures the sensitivity of the call option's price to changes in the stock price. It ranges from 0 (deep out-of-the-money) to 1 (deep in-the-money).

$$
\Delta_C = \frac{\partial C}{\partial S} = \Phi (d_1)
$$


2. **Put Option Delta**: Measures the sensitivity of the put option's price to changes in the stock price. It ranges from -1 (deep in-the-money) to 0 (deep out-of-the-money).

$$
\Delta_P = \frac{\partial P}{\partial S} = \Phi (d_1) - 1
$$


<br>

<center><i> Let's quickly derive these relationships... </i></center>

<br>



#### Call Option Delta



**1. Call Option Price**

$$
C(S, K, \sigma, r,  T) = S \Phi (d_1) - K e^{-rT} \Phi (d_2)
$$

where:

- $S$ = Price of underlying
- $K$ = Option strike price
- $\Phi(.)$ = CDF of Standard Normal Distribution
- $\sigma$ = Implied volatility (IV) of the underlying asset
- $r$ = Risk-free rate
- $T$ = Time remaining to expiry
- $d_1 = \frac{\ln\left(\frac{S}{K}\right) + \left(r + \frac{\sigma^2}{2}\right)T}{\sigma \sqrt{T}}$
- $d_2 = d_1 - \sigma \sqrt{T}$


<br>

**2. Identify Terms Dependent on $S$**
- $S \Phi (d_1)$: Directly depends on $S$ since $S$ is multiplied by $\Phi (d_1)$.
- $K e^{-rT} \Phi (d_2)$: This term does not depend on $S$, so its derivative w.r.t. $S$ is 0.

<br>

**3. Differentiate $S \Phi (d_1)$**
The derivative of $S \Phi (d_1)$ has two components:
- $\Phi (d_1)$: Cumulative distribution of $d_1$, which depends on $S$.
- $d_1$ is:

$$
\begin{aligned}
d_1 &= \frac{\ln\left(\frac{S}{K}\right) + \left(r + \frac{\sigma^2}{2}\right)T}{\sigma \sqrt{T}} \\
\\
\Rightarrow \frac{\partial (S \Phi (d_1))}{\partial S} &= \Phi (d_1) + S \cdot N(d_1) \cdot \frac{\partial d_1}{\partial S} \rightarrow \textit{Using the chain rule}
\end{aligned}
$$

<br>

**4. Simplify $\frac{\partial d_1}{\partial S}$**
From $d_1$:

$$
\frac{\partial d_1}{\partial S} = \frac{1}{S \sigma \sqrt{T}}
$$

<br>

**5. Substituting back:**

$$
\frac{\partial (S \Phi (d_1))}{\partial S} = \Phi (d_1) + S \cdot N(d_1) \cdot \frac{1}{S \sigma \sqrt{T}}
$$


Simplify further:

$$
\frac{\partial (S \Phi (d_1))}{\partial S} = \Phi (d_1)
$$

<br>

**6. Solve for Call Option Delta:**

The derivative of $C$ with respect to $S$ is:

$$
\Delta_C = \Phi (d_1)
$$

$$
\Rightarrow \textit{This is nothing but the standard normal CDF evaluated at } d_1

$$


---

#### Put Option Delta

<br>

**1. Put Option Price**

$$
\begin{aligned}
P(S, K, r, \sigma, T) &= K e^{-rT} \Phi (-d_2) - S \Phi (-d_1)
\\
\vdots
\\
\textit{Similar }& \textit{process...}
\\
\vdots
\\
\Rightarrow \Delta_P &= \frac{\partial P}{\partial S}
\\
\Rightarrow \Delta_P &= \Phi (d_1) - 1
\end{aligned}
$$



#### **Key Intuition**

**What happens when we subtract the put delta from the call delta?**

$$
\begin{align}
\Delta_C -\Delta_P &= \Phi (d_1) - (\Phi (d_1) - 1) \\
\Delta_C -\Delta_P &= 1 \\
\end{align}
$$


$$
\Delta_C \in [0,1] \\
\Delta_P \in [-1, 0] \Rightarrow -\Delta_P \in [0, 1] \\
$$


$$
\begin{align}
\Rightarrow \textit{Call delta + (- put delta) = 1 indicates that if we add the call and (-put) deltas, we would cover the entire probability space of } d_1 \\
\end{align}
$$

<br>

---

### **Question 3: What Is The "Pareto Range" Predicted By The Market Today?**

**Also: What Do I Mean By "Pareto Range"?**

**Brief Note On Data Sources**

Raw data is available from a variety of sources:

- Option prices: WRDS, OptionMetrics, Barchart, Bloomberg etc.

- Futures: ICE / Chicago Mercantile Exchange, other data providers etc.

**Answer:**

*Let's look at the raw data for the option chain for a single trading day.*

In [5]:
asof_date = "2025-02-12"
comdty = "brent"
comdty_root = COMDTY_CODES[comdty]

display_months = {"brent": 15, "wti": 15, "henry_hub": 12}
months_to_display = display_months[comdty]
heatmap_steps = {"brent": 3, "wti": 3, "henry_hub": 1}
interpolation_args = {
    "brent": {"method": "cubic", "order": 3},
    "wti": {"method": "linear", "order": 1},
    "henry_hub": {"method": "quadratic", "order": 3},
}


# get option chain for all commodities
options_data = hf.get_option_chain(comdty, asof_date=asof_date)
display(options_data)
print("Datapoints:", options_data.columns)

symbol root contract underlyingFuture     contractName contractMonth  \
0     CBJ300C   CB    CBJ25            CBJ25  Crude Oil Brent             J   
1     CBJ300P   CB    CBJ25            CBJ25  Crude Oil Brent             J   
2     CBJ350C   CB    CBJ25            CBJ25  Crude Oil Brent             J   
3     CBJ350P   CB    CBJ25            CBJ25  Crude Oil Brent             J   
4     CBJ375C   CB    CBJ25            CBJ25  Crude Oil Brent             J   
...       ...  ...      ...              ...              ...           ...   
8691  CBZ720T   CB    CBZ29            CBZ29  Crude Oil Brent             Z   
8692  CBZ730G   CB    CBZ29            CBZ29  Crude Oil Brent             Z   
8693  CBZ730T   CB    CBZ29            CBZ29  Crude Oil Brent             Z   
8694  CBZ740G   CB    CBZ29            CBZ29  Crude Oil Brent             Z   
8695  CBZ740T   CB    CBZ29            CBZ29  Crude Oil Brent             Z   

     exchange  type  strike expirationDate        date  impliedVolatility  \
0         ICE  Call    30.0     2025-02-25  2025-02-12             2.1220   
1         ICE   Put    30.0     2025-02-25  2025-02-12             1.7127   
2         ICE  Call    35.0     2025-02-25  2025-02-12             1.7624   
3         ICE   Put    35.0     2025-02-25  2025-02-12             1.4393   
4         ICE  Call    37.5     2025-02-25  2025-02-12             1.6021   
...       ...   ...     ...            ...         ...                ...   
8691      ICE   Put    72.0     2029-10-26  2025-02-12             0.2831   
8692      ICE  Call    73.0     2029-10-26  2025-02-12             0.2639   
8693      ICE   Put    73.0     2029-10-26  2025-02-12             0.2840   
8694      ICE  Call    74.0     2029-10-26  2025-02-12             0.2612   
8695      ICE   Put    74.0     2029-10-26  2025-02-12             0.2852   

       delta   gamma   theta    vega   open   high    low   last  \
0     0.9922  0.0006 -0.0152  0.0025  45.18  45.18  45.18  45.18   
1    -0.0013  0.0002 -0.0041  0.0006   0.01   0.01   0.01   0.01   
2     0.9916  0.0008 -0.0136  0.0027  40.18  40.18  40.18  40.18   
3    -0.0016  0.0003 -0.0040  0.0007   0.01   0.01   0.01   0.01   
4     0.9914  0.0009 -0.0128  0.0028  37.68  37.68  37.68  37.68   
...      ...     ...     ...     ...    ...    ...    ...    ...   
8691 -0.3388  0.0076 -0.0020  0.4678  15.46  15.46  15.46  15.46   
8692  0.4588  0.0083 -0.0023  0.4723  10.95  10.95  10.95  10.95   
8693 -0.3456  0.0076 -0.0020  0.4698  16.04  16.04  16.04  16.04   
8694  0.4498  0.0084 -0.0023  0.4743  10.55  10.55  10.55  10.55   
8695 -0.3520  0.0076 -0.0019  0.4715  16.64  16.64  16.64  16.64   

      previousClose  change  percentChange  volume  
0             47.00   -1.82      -3.872340       0  
1              0.01    0.00       0.000000       0  
2             42.00   -1.82      -4.333333       0  
3              0.01    0.00       0.000000       0  
4             39.50   -1.82      -4.607595       0  
...             ...     ...            ...     ...  
8691          15.28    0.18       1.178010       0  
8692          11.30   -0.35      -3.097345       0  
8693          15.85    0.19       1.198738       0  
8694          10.89   -0.34      -3.122130       0  
8695          16.44    0.20       1.216545       0  

[8696 rows x 24 columns]

Datapoints: Index(['symbol', 'root', 'contract', 'underlyingFuture', 'contractName',
       'contractMonth', 'exchange', 'type', 'strike', 'expirationDate', 'date',
       'impliedVolatility', 'delta', 'gamma', 'theta', 'vega', 'open', 'high',
       'low', 'last', 'previousClose', 'change', 'percentChange', 'volume'],
      dtype='object')


--> For the homework, you will need the the option chain for `SPX` options.

--> You will also need the term structure of futures for the underlying security (`SPX` for the homework)

In [6]:
futures_data = hf.get_futures(ticker="CY", asof_date=asof_date)
display(futures_data)
print("Datapoints:", futures_data.columns)

comdty_code comdty_name              comdty_desc  trade_date  \
0           CY   Brent Oil  Brent Financial Futures  2025-02-12   
1           CY   Brent Oil  Brent Financial Futures  2025-02-12   
2           CY   Brent Oil  Brent Financial Futures  2025-02-12   
3           CY   Brent Oil  Brent Financial Futures  2025-02-12   
4           CY   Brent Oil  Brent Financial Futures  2025-02-12   
..         ...         ...                      ...         ...   
81          CY   Brent Oil  Brent Financial Futures  2025-02-12   
82          CY   Brent Oil  Brent Financial Futures  2025-02-12   
83          CY   Brent Oil  Brent Financial Futures  2025-02-12   
84          CY   Brent Oil  Brent Financial Futures  2025-02-12   
85          CY   Brent Oil  Brent Financial Futures  2025-02-12   

    contract_year  contract_month contract_date  future_month_index  \
0            2025               2    2025-02-28                   0   
1            2025               3    2025-03-31                   1   
2            2025               4    2025-04-30                   2   
3            2025               5    2025-05-31                   3   
4            2025               6    2025-06-30                   4   
..            ...             ...           ...                 ...   
81           2031              11    2031-11-30                  81   
82           2031              12    2031-12-31                  82   
83           2032               1    2032-01-31                  83   
84           2032               2    2032-02-29                  84   
85           2032               3    2032-03-31                  85   

    settle_price comdty_unit  open_interest  volume  last_trade_date  
0          75.28       $/Bbl            NaN     NaN              NaN  
1          74.85       $/Bbl            NaN     NaN              NaN  
2          74.47       $/Bbl            NaN     NaN              NaN  
3          74.06       $/Bbl            NaN     NaN              NaN  
4          73.63       $/Bbl            NaN     NaN              NaN  
..           ...         ...            ...     ...              ...  
81         67.64       $/Bbl            NaN     NaN              NaN  
82         67.63       $/Bbl            NaN     NaN              NaN  
83         67.62       $/Bbl            NaN     NaN              NaN  
84         67.62       $/Bbl            NaN     NaN              NaN  
85         67.62       $/Bbl            NaN     NaN              NaN  

[86 rows x 13 columns]

Datapoints: Index(['comdty_code', 'comdty_name', 'comdty_desc', 'trade_date',
       'contract_year', 'contract_month', 'contract_date',
       'future_month_index', 'settle_price', 'comdty_unit', 'open_interest',
       'volume', 'last_trade_date'],
      dtype='object')


In [7]:
if asof_date is None:
    asof_date = options_data["date"][0]

_ = hf.run_prediction_models(
    comdty,
    asof_date,
    months_to_display=months_to_display,
    heatmap_step=heatmap_steps[comdty],
    interpolation_args=interpolation_args,
)

Expiration Date   Feb 2025  Mar 2025  Apr 2025  May 2025  Jun 2025  Jul 2025  \
80% Below            78.00     81.00     83.00     84.50     86.00     87.00   
50/50                75.50     75.00     75.00     75.00     74.50     74.50   
80% Above            72.00     69.50     67.50     65.75     64.50     63.00   
Strip 2025-02-12     75.28     74.85     74.47     74.06     73.63     73.19   

Expiration Date   Aug 2025  Sep 2025  Oct 2025  Nov 2025  Dec 2025  Jan 2026  \
80% Below            88.00     89.00     90.00     91.00     92.00      93.0   
50/50                74.00     74.00     74.00     73.50     73.50      73.5   
80% Above            61.50     60.50     59.50     58.50     57.50      57.0   
Strip 2025-02-12     72.78     72.41     72.07     71.74     71.44      71.2   

Expiration Date   Feb 2026  Mar 2026  Apr 2026  
80% Below            94.00     95.00     95.00  
50/50                73.50     73.50     73.50  
80% Above            56.50     55.50     55.00  
Strip 2025-02-12     70.98     70.79     70.62

## Let's Discuss These Charts...

----

## Progress Check: What Have We Done So Far?

<font color='green' size=6>☑</font> Modeled an E&P as a **long position in Brent oil futures (CME: CY)**.

<font color='green' size=6>☑</font> Working with **real option prices & futures data** for Brent oil.

<font color='green' size=6>☑</font> Use **option delta** to approximate the probability of an option expiring in-the-money.

<font color='red' size=6>☐</font> **Validate option pricing models** using **Monte Carlo simulation** of Brent futures with implied volatility.

<font color='red' size=6>☐</font> Use **option delta** to define acceptable risk ranges for the hedging program (e.g., 80% probability of options expiring worthless).

<font color='red' size=6>☐</font> Design a hedging strategy to **lock in a price floor** for oil using put options.

<font color='red' size=6>☐</font> Attempt to **make the hedge costless** by selling call options (i.e., constructing a **costless collar**).

---

## **The Sanity Check: Validating The Option Market**

### Why Do We Care About Validating the Option Market?

- The market is often prone to periods of **excitement, fear, and uncertainty**.

- At any given point in time, the prices of options will reflect the views of all market participants *in aggregate*.

- You could place a hedging trade at a time of high volatility, and sacrifice potential hedging returns if volatility drops. **Why?**

- Validating market prices against ***some kind*** of theoretical benchmark can provide insight into:
    - Is this a good time to hedge? i.e. are prices chaotic or stable?

    - Are there opportunities for arbitrage?

<br>

---

### 3-Step Approach To Validation:

<br>



#### **Step 1: Build The Volatility Surface**

In [8]:
options_data = hf.get_option_chain(comdty, asof_date)
# add a columns of time remaining to expiration in years, relative to asof_date
options_data = options_data.assign(
    time_to_expiry=(
        options_data["expirationDate"].apply(pd.to_datetime) - pd.to_datetime(asof_date)
    ).dt.days
    / 365
)
options_data.set_index(["time_to_expiry", "type", "strike"], inplace=True)
strip_pricing = hf.get_strip_pricing(asof_date)
# convert index to time-to-expiry
strip_pricing.index = hf.dates_to_time_remaining(strip_pricing.index, asof_date)
strip_pricing = strip_pricing.iloc[:months_to_display]

display_strip_pricing = strip_pricing.copy().to_frame()
display_strip_pricing.index = hf.time_remaining_to_dates(
    display_strip_pricing.index, asof_date
).strftime("%b %Y")
display(
    display_strip_pricing.T.style.set_caption(
        f"Strip Pricing as of {asof_date}"
    ).format("{:.2f}")
)

##### Step 1a: Build the Volatility Surface for OTM Puts

In [9]:
puts, put_iv_surface = hf.build_put_iv_surface(options_data, strip_pricing)
put_price_surface = hf.build_put_price_surface(options_data, strip_pricing)
hf.plot_vol_price_charts(
    iv_surface=put_iv_surface,
    price_surface=put_price_surface,
    strike_range=[
        np.floor(put_iv_surface.index.min()),
        np.ceil(put_iv_surface.index.max()),
    ],
    expiry_range=[put_iv_surface.columns.min(), put_iv_surface.columns.max()],
    iv_surface_title="Put Implied Volatility Surface",
    price_surface_title="Put Price Surface",
)

##### Step 1b: Build the Volatility Surface for Calls

In [10]:
calls, call_iv_surface = hf.build_call_iv_surface(options_data, strip_pricing)
call_price_surface = hf.build_call_price_surface(options_data, strip_pricing)
hf.plot_vol_price_charts(
    iv_surface=call_iv_surface,
    price_surface=call_price_surface,
    strike_range=[
        np.floor(call_iv_surface.index.min()),
        np.ceil(call_iv_surface.index.max()),
    ],
    expiry_range=[call_iv_surface.columns.min(), call_iv_surface.columns.max()],
    iv_surface_title="Call Implied Volatility Surface",
    price_surface_title="Call Price Surface",
)

##### Step 1c: Build The Complete Volatility Surface

In [11]:
iv_surface = hf.build_full_iv_surface(
    put_iv_surface, call_iv_surface, strike_range=(35, 150), expiry_range=(0.01, 2.0)
)

price_surface = hf.build_full_price_surface(
    put_price_surface,
    call_price_surface,
    strike_range=(35, 150),
    expiry_range=(0.01, 2.0),
)

hf.plot_vol_price_charts(
    iv_surface=iv_surface,
    price_surface=price_surface,
    strike_range=[np.floor(iv_surface.index.min()), np.ceil(iv_surface.index.max())],
    expiry_range=[iv_surface.columns.min(), iv_surface.columns.max()],
    iv_surface_title="Brent Oil Implied Volatility Surface",
    price_surface_title="Brent Oil Price Surface",
)

#### **Step 2: Simulate How The Futures Might Move (Based on IV Surface)**

- Our approach to simulating Brent futures involves a random simulation of *each Brent futures contract*.

- We simulate the movement of the futures strip using *GBM (Geometric Brownian Motion) with constant drift equal to the long-term risk-free rate, and dynamic volatility, based on the current market implied volatility surface.*

- Updating the simulated volatility dynamically at each step ensures that as simulated prices move away from the current price level, subsequent simulated prices *incorporate the volatility that the market is using to price options at that level.*

<br>

<center> <font color='red'><i>! Important !:</font> This is merely one approach to Monte Carlo simulation. Different researchers can use different approaches (e.g. dynamic risk-free rates, different volatility models etc).</i></center>



**Concrete Example**

1. In concrete terms, assume we are simulating the *February 2025 Brent oil futures contract*, which settled at *\$78.50* on a particular date (say, January 13, 2025). This contract will continue trading until *January 31, 2025*.

2. We reference the option chain as of this date, and look for the option contract (call or put) with a strike price *closest to \$78.50*, and extract the implied volatility (IV) of this option from the IV surface (say, 28% annualized).

3. This IV is then used as the starting volatility term in the random simulation, which needs to be run until the contract expiration, or *(31 - 13) = 18 days*.

4. For each iteration (each day) of the random simulation, the IV term is updated based on the IV surface calculated earlier. e.g. If the second price in the simulation is \$81.54, the model updates the IV based on the option with the nearest strike price, which could be *higher, lower, or equal to 28%.*

5. This approach allows the simulated prices movement to mimic the volatility of actual prices as they deviate further from the current price level (the strip). For instance, option prices significantly higher than the current price level typically exhibit higher volatility (higher likelihood of changing up or down).


In [12]:
# print(comdty_code)
comdty_code = "CY"
r = 0.045
N = 500
dt = 1 / 365.0
show_charts = False

simulated_futures = hf.build_simulated_futures(
    asof_date,
    strip_pricing,
    iv_surface,
    months_to_display,
    comdty_code,
    r,
    N,
    dt,
    show_charts,
)

#### **Step 3: Choosing Risk Ranges And Constructing The Costless Collar**

1. Now that we have a volatility surface and a MC simulation of the futures curve, we can examine the market pricing of options, and determine **what floor/ceiling combination might be costless**, based on the prior day's closing prices.
2. For instance, say we want a collar that has a **floor put price at the 20th percentile level** (meaning there is an 80% chance the price will be above this level), we want to be able to answer the question:

    *What is the ceiling (call) strike price that would completely offset the cost of this floor?*

3. We introduce the input parameter `delta` or `d`, `0% < d < 100%`, which gives us the collar strike range of `(d, 1-d)`. If `d = 0.80`, this would result in the model finding `80/20` collars.

In [13]:
# enter the range of costless collar to construct
d = 0.80
print(f"Constructing a {d:.0%} / {(1 - d):.0%} collar...")

# build the delta map
delta_map = hf.build_delta_map(
    comdty,
    asof_date,
    months_to_display,
    show_detail=False,
    weighted=False,
    interpolate_missing=True,
    interpolation_args=interpolation_args,
)


# simulate a range of futures, including the collar strike %iles
default_percentiles = np.unique(
    np.round(np.sort(np.append(np.arange(0.1, 1.0, 0.1), np.array([d, 1 - d]))), 3)
)


simulated_futures = hf.simulate_futures(
    asof_date,
    strip_pricing,
    iv_surface,
    r,
    N,
    dt,
    default_percentiles=default_percentiles,
    show_charts=True,
    random_seed=123,
)

collar_strikes, costless_collars = hf.show_collar_strikes(
    d,
    delta_map,
    sim_d=simulated_futures.loc[:, [f"{d:.0%}", f"{1 - d:.0%}"]],
    months_to_display=months_to_display,
    asof_date=asof_date,
    options_data=options_data,
)

simulated_futures.index = collar_strikes.index

display(simulated_futures)

Constructing a 80% / 20% collar...


Simulated 500 paths for each contract.


Net cost to hedge this set of collars: $-0.1744 per unit


10%        20%        30%        40%        50%  \
expirationDate                                                          
2025-02-28      71.379119  72.825257  74.134570  74.878030  75.430146   
2025-03-31      66.937784  70.477147  72.260252  74.159948  75.428520   
2025-04-30      64.797611  68.708983  70.942812  73.107622  75.223709   
2025-05-31      62.876768  66.421503  70.337213  73.141360  75.365367   
2025-06-30      60.725490  65.656326  69.073507  72.081107  74.890939   
2025-07-31      59.164556  64.355500  68.169664  71.203102  74.226868   
2025-08-31      57.692838  63.147748  66.673634  70.944024  74.305199   
2025-09-30      54.762347  62.387216  66.374230  70.030779  73.456341   
2025-10-31      54.703424  60.211345  65.293109  69.492024  73.330418   
2025-11-30      53.852721  59.566391  64.509457  69.564989  73.520332   
2025-12-31      52.505189  59.024435  63.721977  69.529700  74.260283   
2026-01-31      52.175654  58.926913  64.236587  68.823089  74.379530   
2026-02-28      51.076737  57.768753  64.248275  69.042128  74.441892   
2026-03-31      48.802864  58.503941  63.684583  69.933945  74.464064   
2026-04-30      48.960612  57.897326  63.294054  69.244821  73.988963   

                      60%        70%        80%         90%  \
expirationDate                                                
2025-02-28      76.296566  77.579383  78.557281   80.160832   
2025-03-31      77.241339  78.850082  81.362657   83.738605   
2025-04-30      77.436369  79.781499  82.874456   86.431862   
2025-05-31      77.975230  80.828667  84.239133   89.054440   
2025-06-30      77.713381  80.741714  84.023854   90.483143   
2025-07-31      77.762430  81.191231  86.329783   93.023513   
2025-08-31      77.545635  81.556143  86.333770   94.265513   
2025-09-30      76.973500  82.404329  86.212695   95.286658   
2025-10-31      77.423074  81.732974  87.584422   95.837373   
2025-11-30      77.824431  82.685070  88.620979   97.861046   
2025-12-31      78.780756  83.420812  88.997411   99.487889   
2026-01-31      78.678809  84.122648  90.325719   99.843970   
2026-02-28      79.339299  84.657334  91.391220  101.433318   
2026-03-31      79.429639  85.087504  91.672064  103.491689   
2026-04-30      79.885276  83.765108  92.337339  105.532936   

                Strip Feb 12, 2025  
expirationDate                      
2025-02-28                   75.28  
2025-03-31                   74.85  
2025-04-30                   74.47  
2025-05-31                   74.06  
2025-06-30                   73.63  
2025-07-31                   73.19  
2025-08-31                   72.78  
2025-09-30                   72.41  
2025-10-31                   72.07  
2025-11-30                   71.74  
2025-12-31                   71.44  
2026-01-31                   71.20  
2026-02-28                   70.98  
2026-03-31                   70.79  
2026-04-30                   70.62

---

## Progress Check: What Did We Just Do?

<font color='green' size=6>☑</font> Modeled an E&P as a **long position in Brent oil futures (CME: CY)**.

<font color='green' size=6>☑</font> Working with **real option prices & futures data** for Brent oil.

<font color='green' size=6>☑</font> Use **option delta** to approximate the probability of an option expiring in-the-money.

<font color='green' size=6>☑</font> **Validate option pricing models** using **Monte Carlo simulation** of Brent futures with implied volatility.

<font color='green' size=6>☑</font> Use **option delta** to define acceptable risk ranges for the hedging program (e.g., 80% probability of options expiring worthless).

<font color='green' size=6>☑</font> Design a hedging strategy to **lock in a price floor** for oil using put options.

<font color='green' size=6>☑</font> Attempt to **make the hedge costless** by selling call options (i.e., constructing a **costless collar**).

---


## Bridge to SPX Options Homework

- Assume client has a long SPX position

    - You will pull the option chain for SPX from WRDS (code will be provided for the raw data pull).

    - You will construct dataframes that work with the charting functions provided.

    - You will output a dashboard that allows the user to select a **risk range desired for the costless collar hedge**, and returns the strikes available.
